## refs
- https://towardsdatascience.com/dbscan-algorithm-complete-guide-and-application-with-python-scikit-learn-d690cbae4c5d
- https://hdbscan.readthedocs.io/en/latest/comparing_clustering_algorithms.html#
- https://github.com/gboeing/2014-summer-travels/blob/master/clustering-scikitlearn.ipynb

In [24]:
import json
import time # unused?
import csv
import seaborn as sns
import numpy as np # +dep
import pandas as pd # +dep
import matplotlib.pyplot as plt # interactive notebook
#import seaborn as sns # unused?
import matplotlib as mpl
# mappings, interactive notebook
#import cartopy
import folium

In [25]:
# raw NRT data
import pathlib
#data = pd.read_csv(str(pathlib.Path("/home/jkp/Documents/agni/extras/fire.csv").resolve()))
data_y2019 = pd.read_csv(str(pathlib.Path("/home/jkp/Documents/agni/extras/hotspots_data_2019.csv").resolve()))
#data = pd.read_csv(str(pathlib.Path("/home/jkp/Documents/agni/extras/hotspots_data_2019.csv").resolve()))
#data = pd.read_csv(str(pathlib.Path("/home/jkp/Documents/agni/extras/ARIMA-train-day1.csv"...).resolve()))
#data2 = pd.read_csv(str(pathlib.Path("/home/jkp/Documents/agni/extras/ARIMA-train-day2.csv").resolve()))
filtered_data = data_y2019[data_y2019.acq_date.str.contains('2019-03')].append(data_y2019[data_y2019.acq_date.str.contains('2019-04')])
filtered_data.acq_date.unique()
data_y2019.head()

latitude   longitude  bright_ti4  scan  track    acq_date  acq_time  \
0  14.373807  100.632462      326.08  0.34   0.56  2019-01-01       557   
1  14.378959  100.631424      341.67  0.34   0.56  2019-01-01       557   
2  14.624126  102.694824      334.70  0.50   0.49  2019-01-01       557   
3  14.395066  102.168671      328.69  0.54   0.51  2019-01-01       557   
4  14.996263  104.727219      335.78  0.55   0.43  2019-01-01       557   

  satellite instrument confidence  version  bright_ti5   frp  type  
0         N      VIIRS          n        1      281.98  2.49     0  
1         N      VIIRS          n        1      283.59  2.49     0  
2         N      VIIRS          n        1      286.68  4.82     0  
3         N      VIIRS          n        1      288.09  4.43     0  
4         N      VIIRS          n        1      299.92  4.33     0

In [26]:
import math

GRIDS = 100
hotspots_counts = np.zeros((GRIDS,GRIDS))

pi = math.pi
r_earth = 6371000.0 #m
lat = 17.779913 
lon = 97.715363
dy2 = 350
dx2 = 350
lat_step =  (dy2 / r_earth) * (180 / pi)
lon_step =  (dx2 / r_earth) * (180 / pi) / math.cos(lat * pi/180)

lons = np.arange(lon,lon+lon_step*100,lon_step)
lats = np.arange(lat,lat+lat_step*100,lat_step)
print(len(lons))
print(len(lats))
print('sample lat : ',lats[1],lats[2],lats[3])
print('sample lon : ',lons[1],lons[2],lons[3])

101
101
sample lat :  17.783060625620717 17.786208251241433 17.78935587686215
sample lon :  97.7186685082432 97.7219740164864 97.7252795247296


In [27]:
#april_data = pd.read_csv(str(pathlib.Path("/home/jkp/Documents/agni/extras/firem04-m05.csv").resolve()))
april_data = filtered_data
april_data.head()
unique_date = april_data.acq_date.unique()
#unique_date = ['2019-04-01','2019-04-02']
print(unique_date)

['2019-03-01' '2019-03-02' '2019-03-03' '2019-03-04' '2019-03-05'
 '2019-03-06' '2019-03-07' '2019-03-08' '2019-03-09' '2019-03-10'
 '2019-03-11' '2019-03-12' '2019-03-13' '2019-03-14' '2019-03-15'
 '2019-03-16' '2019-03-17' '2019-03-18' '2019-03-19' '2019-03-20'
 '2019-03-21' '2019-03-22' '2019-03-23' '2019-03-24' '2019-03-25'
 '2019-03-26' '2019-03-27' '2019-03-28' '2019-03-29' '2019-03-30'
 '2019-03-31' '2019-04-01' '2019-04-02' '2019-04-03' '2019-04-04'
 '2019-04-05' '2019-04-06' '2019-04-07' '2019-04-08' '2019-04-09'
 '2019-04-10' '2019-04-11' '2019-04-12' '2019-04-13' '2019-04-14'
 '2019-04-15' '2019-04-16' '2019-04-17' '2019-04-18' '2019-04-19'
 '2019-04-20' '2019-04-21' '2019-04-22' '2019-04-23' '2019-04-24'
 '2019-04-25' '2019-04-26' '2019-04-27' '2019-04-28' '2019-04-29'
 '2019-04-30']


In [28]:
count_results = []
GRIDS = len(lats)
for days in unique_date:
    source = april_data
    read_data = source[april_data.acq_date.eq(days)]
    hotspots_counts = np.ones((GRIDS,GRIDS))
    for i,r in read_data.iterrows():
        for b1 in range(GRIDS):
            if lats[b1] - (lat_step/2) <= r['latitude'] < lats[b1] + (lat_step/2):
                for b2 in range(GRIDS):
                    if lons[b2] - (lon_step/2 ) <= r['longitude'] < lons[b2] + (lon_step/2):
                        hotspots_counts[b1,b2] = 2
                        #hotspots_counts[b1,b2] += 1
    count_results.append(hotspots_counts)

In [43]:
count_results[45][78][16]
#[day][row][col]
unique_date[30]

'2019-03-31'

In [6]:
for i in count_results[30]:
    for y in i:
        if y == 2:
            print(y)

2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0
2.0


In [7]:
import numpy as np
import matplotlib.pyplot as plt
from matplotlib import animation
from matplotlib import colors
%matplotlib
# Create a forest fire animation based on a simple cellular automaton model.
# The maths behind this code is described in the scipython blog article
# at https://scipython.com/blog/the-forest-fire-model/
# Christian Hill, January 2016.

# Displacements from a cell to its eight nearest neighbours
neighbourhood = ((-1,-1), (-1,0), (-1,1), (0,-1), (0, 1), (1,-1), (1,0), (1,1))
EMPTY, TREE, FIRE = 0, 1, 2
# Colours for visualization: brown for EMPTY, dark green for TREE and orange
# for FIRE. Note that for the colormap to work, this list and the bounds list
# must be one larger than the number of different values in the array.
colors_list = [(0.2,0,0), (0,0.5,0), (1,0,0), 'orange']
cmap = colors.ListedColormap(colors_list)
bounds = [0,1,2,3]
norm = colors.BoundaryNorm(bounds, cmap.N)

def iterate(X):
    """Iterate the forest according to the forest-fire rules."""

    # The boundary of the forest is always empty, so only consider cells
    # indexed from 1 to nx-2, 1 to ny-2
    X1 = np.zeros((ny, nx))
    for ix in range(1,nx-1):
        for iy in range(1,ny-1):
            
            if X[iy,ix] == EMPTY and np.random.random() <= p:
                X1[iy,ix] = TREE
                
            if X[iy,ix] == TREE:
                X1[iy,ix] = TREE
                for dx,dy in neighbourhood:
                    if X[iy+dy,ix+dx] == FIRE:
                        X1[iy,ix] = FIRE
                        break
            else:
                if np.random.random() <= f:
                    X1[iy,ix] = FIRE
    return X1
# The initial fraction of the forest occupied by trees.
forest_fraction = 0.2
# Probability of new tree growth per empty cell, and of lightning strike.
p, f = 0.05, 0.001
# Forest size (number of cells in x and y directions).
nx, ny = 101, 101
# Initialize the forest grid.
X  = np.zeros((ny, nx))
X[1:ny-1, 1:nx-1] = np.random.randint(0, 2, size=(ny-2, nx-2))
X[1:ny-1, 1:nx-1] = np.random.random(size=(ny-2, nx-2)) < forest_fraction

fig = plt.figure(figsize=(25/3, 6.25))
ax = fig.add_subplot(111)
ax.set_axis_off()
im = ax.imshow(X, cmap=cmap, norm=norm)#, interpolation='nearest')

# The animation function: called to produce a frame for each generation.
def animate(i):
    im.set_data(animate.X)
    animate.X = iterate(animate.X)
# Bind our grid to the identifier X in the animate function's namespace.
animate.X = X

# Interval between frames (ms).
interval = 52
anim = animation.FuncAnimation(fig, animate, interval=interval)
plt.show()

Using matplotlib backend: TkAgg


In [30]:
neighbourhood = ((-1,-1), (-1,0), (-1,1), (0,-1), (0, 1), (1,-1), (1,0), (1,1))
EMPTY, TREE, FIRE = 0, 1, 2
colors_list = [(0.2,0,0), (0,0.5,0), (1,0,0), 'orange']
cmap = colors.ListedColormap(colors_list)
bounds = [0,1,2,3]
norm = colors.BoundaryNorm(bounds, cmap.N)

X  = np.zeros((ny, nx))
X[1:ny-1, 1:nx-1] = np.random.randint(0, 2, size=(ny-2, nx-2))
X[1:ny-1, 1:nx-1] = np.random.random(size=(ny-2, nx-2)) < forest_fraction
plt.imshow(count_results[30],origin='lower',cmap=cmap,norm=norm)
plt.show()

In [31]:
plt.imshow(count_results[32],origin='lower',cmap=cmap,norm=norm)
plt.show()

In [32]:
EMPTY, TREE, FIRE = 0,1,2
def iterate(X):
    """Iterate the forest according to the forest-fire rules."""

    # The boundary of the forest is always empty, so only consider cells
    # indexed from 1 to nx-2, 1 to ny-2
    X1 = np.zeros((ny, nx))
    for ix in range(1,nx-1):
        for iy in range(1,ny-1):
            if X[iy,ix] == FIRE:
                X1[iy,ix] = EMPTY
            if X[iy,ix] == TREE:
                X1[iy,ix] = TREE
                for dx,dy in neighbourhood:
                    if X[iy+dy,ix+dx] == FIRE:
                        X1[iy,ix] = FIRE
                        break
    return X1


colors_list = [(0.2,0,0), (0,0.5,0), (1,0,0), 'orange']
cmap = colors.ListedColormap(colors_list)
bounds = [0,1,2,3]
norm = colors.BoundaryNorm(bounds, cmap.N)

X  = count_results[31]

Y = iterate(X)
Z = iterate(Y)

#plt.imshow(Y)
#plt.show()
fig = plt.figure()
ax1 = fig.add_subplot(2,3,1)
ax1.set_title('X')
ax1.imshow(X,cmap=cmap,norm=norm)
ax2 = fig.add_subplot(2,3,2)
ax2.set_title('Y')
ax2.imshow(Y,cmap=cmap,norm=norm)
ax3 = fig.add_subplot(2,3,3)
ax3.set_title('Z')
ax3.imshow(Z,cmap=cmap,norm=norm)
ax4 = fig.add_subplot(2,3,4)
ax4.set_title('d1')
ax4.imshow(count_results[29],cmap=cmap,norm=norm)
ax5 = fig.add_subplot(2,3,5)
ax5.set_title('d2')
ax5.imshow(count_results[30],cmap=cmap,norm=norm)
ax6 = fig.add_subplot(2,3,6)
ax6.set_title('d3')
ax6.imshow(count_results[31],cmap=cmap,norm=norm)
plt.tight_layout()

In [33]:
area = count_results[32]
def markEmptyArea(data,firstIDX,lastIDX):
    empty_lands = np.ones((GRIDS,GRIDS))
    for i in range(firstIDX,lastIDX):
        print(i)
        tmp = data[i]
        for ix in range(1,nx-1):
            for iy in range(1,ny-1):
                #change old fire to empty lands
                if tmp[iy,ix] == FIRE:
                    empty_lands[iy,ix] = EMPTY
    return empty_lands
def markFire(lands,fire):
    for ix in range(1,nx-1):
        for iy in range(1,ny-1):
            #change old fire to empty lands
            if fire[iy,ix] == FIRE:
                lands[iy,ix] = FIRE
    return lands
markedEmpty = markEmptyArea(count_results,21,35)
markedFire = markFire(markedEmpty,count_results[35])
plt.imshow(markedEmpty,cmap=cmap,norm=norm)
plt.show()

21
22
23
24
25
26
27
28
29
30
31
32
33
34


In [34]:
B = iterate(markedFire)
plt.imshow(B,cmap=cmap,norm=norm)

In [176]:
for i in range(0,5):
    print(i)

0
1
2
3
4


In [41]:
import pyproj
import math

#source https://stackoverflow.com/questions/7477003/calculating-new-longitude-latitude-from-old-n-meters
lat = 17.779913 
lon = 97.715363
# lat = 19.540684
# lon = 97.841248
pi = math.pi
r_earth = 6371000.0 #m

# dy = 350
# dx = 350
# new_lat  = lat  - (dy / r_earth) * (180 / pi);
# new_lon = lon - ((dx / r_earth) * (180 / pi) / math.cos(lat * pi/180));
# print(new_lat,new_lon)

# #test grid from 1 virrs coord
lmap = folium.Map(location=[lat, lon], zoom_start=15)
# plots = []
# plot = {}
# plot['latitude'] = lat
# plot['longitude'] = lon
# plots.append(plot)
# plot = {}
# plot['latitude'] = new_lat
# plot['longitude'] = new_lon
# plots.append(plot)
# folium.CircleMarker(location=(lat, lon),
#                         radius=6, fill_color='green', fill_opacity=1,
#                         popup="old"
#                         ).add_to(lmap)
# folium.CircleMarker(location=(new_lat, new_lon),
#                         radius=6, fill_color='blue', fill_opacity=1,
#                         popup="new"
#                         ).add_to(lmap)
dy2 = 350/2
dx2 = 350/2
step_lat =  (dy2 / r_earth) * (180 / pi)
step_lon =  (dx2 / r_earth) * (180 / pi) / math.cos(lat * pi/180)

#draw one grid
points = [(lat-step_lat,lon-step_lon),(lat+step_lat,lon+step_lon)]
folium.Rectangle(bounds=points,fill=True,color = 'red',fill_color = '#940091',fill_opacity=0,weight=1).add_to(lmap)

#more grid
target = B
start_lon = lon
curr_lat = lat
curr_lon  = start_lon
draw_b1=0
for ix in range(0,GRIDS):
    draw_b2 = 0
    for iy in range(0,GRIDS):
        points = [(curr_lat-step_lat,curr_lon-step_lon),(curr_lat+step_lat,curr_lon+step_lon)]
        if target[ix,iy] == FIRE:
            opa = 1
            folium.Rectangle(bounds=points,fill=True,color = 'black',fill_color = 'red',fill_opacity=opa,weight=1).add_to(lmap)
        elif target[ix,iy] == TREE:
            opa = 0.5
            folium.Rectangle(bounds=points,fill=True,color = 'black',fill_color = 'green',fill_opacity=opa,weight=1).add_to(lmap)
        
        draw_b2+=1
        curr_lon += step_lon*2
        
    draw_b1+=1
    curr_lat += step_lat*2
    curr_lon = start_lon

#plot data
data = data_y2019[data_y2019.acq_date.str.contains('2019-04-06')]
for _, row in data.iterrows():
    folium.CircleMarker(location=(row['latitude'], row['longitude']),
                        radius=6, fill_color='red', fill_opacity=1,
                        popup="<b>lat</b>: {} <b>lon</b>: {}".format(row['latitude'],row['longitude'])
                        ).add_to(lmap)
    points = [(row['latitude']-step_lat,row['longitude']-step_lon),(row['latitude']+step_lat,row['longitude']+step_lon)]
    #folium.Rectangle(bounds=points,fill=False,color = 'red',weight=1).add_to(lmap)
lmap

In [187]:
unique_date[35]

'2019-04-05'

In [192]:
FIRE

2